In [1]:
%useLatestDescriptors
%use lets-plot
%use dataframe

# Load data

In [2]:
import org.um.feri.ears.algorithms.gp.GPAlgorithmExecutor
import org.um.feri.ears.util.gp_stats.GPAlgorithmMultiConfigurationsProgressData
import org.um.feri.ears.util.gp_stats.GPProgramSolutionSimple

var dataFile = "C:\\Users\\marko\\UnityProjects\\GenIATraP_refactor\\GeneralTrainingEnvironmentForMAS\\evo_monitor\\src\\data\\multiConfigurationPrograssData.ser"
var progressData = GPAlgorithmMultiConfigurationsProgressData.deserializeState(dataFile)
System.out.println("Progress data loaded from file: " + progressData)

System.out.println("Data size: " +progressData.multiConfigurationProgressData.size)

Progress data loaded from file: org.um.feri.ears.util.gp_stats.GPAlgorithmMultiConfigurationsProgressData@233772f6
Data size: 1


# Prepare helper classes & functions

In [3]:
class SelectedIndividual(
    var selectedConfiguration: Int,
    var selectedRun: Int,
    var selectedGeneration: Int,
    var bestWorstIndividual: Int, // 0 = best, 1 = worst
) {
    constructor() : this(0, 0, 0, 0)
}

In [17]:
import org.um.feri.ears.individual.representations.gp.IndividualMatchResult

fun sumIndividualValues(individualMatchResult: IndividualMatchResult, sumAbsValues: Boolean = false): Double {
    var sum = 0.0
    for (key in individualMatchResult.individualValues.keys) {
        if(sumAbsValues){
            sum += Math.abs(individualMatchResult.individualValues[key]!!)
        }
        else {
            sum += individualMatchResult.individualValues[key]!!
        }
    }

    return sum
}

In [18]:
import org.yaml.snakeyaml.util.Tuple

// Prepare data (best, worst and average individual rating per generation)
fun prepareData(selectedConfiguration: Int, selectedRun: Int, bestGenIndividualsRating: MutableList<GPProgramSolutionSimple>?, worstGenIndividualsRating: MutableList<GPProgramSolutionSimple>?, avgGenIndividualRatings: MutableList<Double>?, bestGenIndividualsRatingAvgFitness: MutableList<Double>?, bestGenIndividualAvgFitnesses: MutableList<GPProgramSolutionSimple>?, worstGenIndividualAvgFitnesses: MutableList<GPProgramSolutionSimple>?, avgGenIndividualAvgFitnesses: MutableList<Double>?){

    var multiConfigurationProgressData = progressData.multiConfigurationProgressData[selectedConfiguration]
    var multiRunProgressData = multiConfigurationProgressData.multiRunProgressData[selectedRun]

    for (genProgressData in multiRunProgressData.gensProgressData) {
        var bestGenIndividualRating = genProgressData.population[0]
        var worstIndividualRating = genProgressData.population[0]
        var avgGenIndividualRating = 0.0

        var bestGenIndividualAvgFitness = genProgressData.population[0]
        var worstIndividualAvgFitness = genProgressData.population[0]
        var avgGenIndividualAvgFitness = 0.0

        for (solution in genProgressData.population) {
            if (solution.finalIndividualFitness.additionalValues["Rating"]!! < bestGenIndividualRating.finalIndividualFitness.additionalValues["Rating"]!!) {
                bestGenIndividualRating = solution
            }

            if (solution.finalIndividualFitness.additionalValues["Rating"]!! > worstIndividualRating.finalIndividualFitness.additionalValues["Rating"]!!) {
                worstIndividualRating = solution
            }

            if(sumIndividualValues(solution.finalIndividualFitness.avgMatchResult) < sumIndividualValues(bestGenIndividualAvgFitness.finalIndividualFitness.avgMatchResult)) {
                bestGenIndividualAvgFitness = solution
            }

            if(sumIndividualValues(solution.finalIndividualFitness.avgMatchResult) > sumIndividualValues(worstIndividualAvgFitness.finalIndividualFitness.avgMatchResult)) {
                worstIndividualAvgFitness = solution
            }

            avgGenIndividualRating += solution.finalIndividualFitness.additionalValues["Rating"]!!
            avgGenIndividualAvgFitness += sumIndividualValues(solution.finalIndividualFitness.avgMatchResult)
        }

        if (bestGenIndividualsRating != null) {
            bestGenIndividualsRating.add(bestGenIndividualRating)
        }
        if (worstGenIndividualsRating != null) {
            worstGenIndividualsRating.add(worstIndividualRating)
        }

        avgGenIndividualRating /= genProgressData.population.size
        if (avgGenIndividualRatings != null) {
            avgGenIndividualRatings.add(avgGenIndividualRating)
        }

        if(bestGenIndividualsRatingAvgFitness != null){
            bestGenIndividualsRatingAvgFitness.add(sumIndividualValues(bestGenIndividualRating.finalIndividualFitness.avgMatchResult))
        }

        if (bestGenIndividualAvgFitnesses != null) {
            bestGenIndividualAvgFitnesses.add(bestGenIndividualAvgFitness)
        }
        if (worstGenIndividualAvgFitnesses != null) {
            worstGenIndividualAvgFitnesses.add(worstIndividualAvgFitness)
        }

        avgGenIndividualAvgFitness /= genProgressData.population.size
        if (avgGenIndividualAvgFitnesses != null) {
            avgGenIndividualAvgFitnesses.add(avgGenIndividualAvgFitness)
        }
    }
}

In [6]:
// TODO Move this to GPProgramSolutionSimple
fun calculateDiversity(solution1: GPProgramSolutionSimple, solution2: GPProgramSolutionSimple, w1: Double, w2: Double) : Double {
    var nodeCountDiversity = 0.0

    // Gather all different node count key
    val nodeCountKeys = mutableSetOf<String>()
    nodeCountKeys.addAll(solution1.nodeCounts.keys)
    nodeCountKeys.addAll(solution2.nodeCounts.keys)

    // Calculate node count diversity
    for (key in nodeCountKeys) {
        val nodeCount1 = solution1.nodeCounts[key] ?: 0
        val nodeCount2 = solution2.nodeCounts[key] ?: 0
        nodeCountDiversity += Math.abs(nodeCount1 - nodeCount2)
    }

    // Normalize node count diversity
    nodeCountDiversity /= (solution1.treeSize + solution2.treeSize)

    // Calculate avg fitness diversity
    var avgFitnessDiversity = 0.0

    // Gather all different avg fitness individual values key
    val avgFitnessKeys = mutableSetOf<String>()
    avgFitnessKeys.addAll(solution1.finalIndividualFitness.avgMatchResult.individualValues.keys)
    avgFitnessKeys.addAll(solution2.finalIndividualFitness.avgMatchResult.individualValues.keys)

    // Calculate avg fitness diversity
    for (key in avgFitnessKeys) {
        val avgFitness1 = solution1.finalIndividualFitness.avgMatchResult.individualValues[key] ?: 0.0
        val avgFitness2 = solution2.finalIndividualFitness.avgMatchResult.individualValues[key] ?: 0.0

        avgFitnessDiversity += Math.abs(avgFitness1 - avgFitness2)
    }

    // Normalize avg fitness diversity
    avgFitnessDiversity /= (Math.abs(sumIndividualValues(solution1.finalIndividualFitness.avgMatchResult, true)) + Math.abs(sumIndividualValues(solution2.finalIndividualFitness.avgMatchResult, true)))

    // Calculate final diversity
    return w1 * avgFitnessDiversity + w2 * nodeCountDiversity
}

# Visualize data (line plot) - Best, worst and average individual rating per generation

In [33]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
// Input params for visualization END

// Prepare data
val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
val worstGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
val avgGenIndividualRatings = mutableListOf<Double>()
val bestGenIndividualsRatingAvgFitness = mutableListOf<Double>()

val bestGenIndividualAvgFitnesses = mutableListOf<GPProgramSolutionSimple>()
val worstGenIndividualAvgFitnesses = mutableListOf<GPProgramSolutionSimple>()
val avgGenIndividualAvgFitnesses = mutableListOf<Double>()

prepareData(selectedConfiguration, selectedRun, bestGenIndividualsRating, worstGenIndividualsRating, avgGenIndividualRatings, bestGenIndividualsRatingAvgFitness, bestGenIndividualAvgFitnesses, worstGenIndividualAvgFitnesses, avgGenIndividualAvgFitnesses)

var multiConfigurationProgressData = progressData.multiConfigurationProgressData[selectedConfiguration]
var multiRunProgressData = multiConfigurationProgressData.multiRunProgressData[selectedRun]

var lastPhaseName = "";
val generations = mutableListOf<String>()
for (genProgressData in multiRunProgressData.gensProgressData) {
    generations.add(genProgressData.generation.toString() + genProgressData.executionPhaseName.substring(genProgressData.executionPhaseName.length - 6, genProgressData.executionPhaseName.length))
}

// Display data
val dfRating = dataFrameOf(
    "Generation" to generations + generations + generations,
    "Rating" to bestGenIndividualsRating.map { it.finalIndividualFitness.additionalValues["Rating"]!! } + worstGenIndividualsRating.map { it.finalIndividualFitness.additionalValues["Rating"]!! } + avgGenIndividualRatings,
    "Individual" to List(generations.size) { "Best" } + List(generations.size) { "Worst" } + List(generations.size) { "Average" }
)

val dfRatingAvgFitness = dataFrameOf(
    "Generation" to generations,
    "AvgFitness" to bestGenIndividualsRatingAvgFitness,
    "Individual" to List(generations.size) { "Average" }
)

val dfAvgFitness = dataFrameOf(
    "Generation" to generations + generations + generations,
    "AvgFitness" to bestGenIndividualAvgFitnesses.map { sumIndividualValues(it.finalIndividualFitness.avgMatchResult) } + worstGenIndividualAvgFitnesses.map { sumIndividualValues(it.finalIndividualFitness.avgMatchResult) } + avgGenIndividualAvgFitnesses,
    "Individual" to List(generations.size) { "Best" } + List(generations.size) { "Worst" } + List(generations.size) { "Average" }
)

// The plot variable stores a plot with the temperature values for each city
val linePlotRating =
    letsPlot(dfRating.toMap()) { x = "Generation"; y = "Rating"; color = "Individual"} + ggsize(2000,800) + geomPoint(shape = 20) + geomLine() + ggtitle("Best Generation Rating")

val linePlotRatingAvgFitness =
    letsPlot(dfRatingAvgFitness.toMap()) { x = "Generation"; y = "AvgFitness"; color = "Individual"} + ggsize(2000,800) + geomPoint(shape = 20) + geomLine() + ggtitle("Best Generation Rating (Average fitness)")

val linePlotAvgFitness =
    letsPlot(dfAvgFitness.toMap()) { x = "Generation"; y = "AvgFitness"; color = "Individual"} + ggsize(2000,800) + geomPoint(shape = 20) + geomLine() + ggtitle("Best Generation Average fitness")

val plots = listOf(linePlotRating, null, linePlotRatingAvgFitness, null, linePlotAvgFitness, null)
gggrid(plots, ncol=2)

<path d="M0.3894146011526255 99.27103228235286 L0.3894146011526255 99.27103228235286 L2.3364876069157527 96.50170763085742 L4.2835606126788806 92.80598894248553 L6.230633618442008 94.7845510350241 L8.177706624205134 95.25089962762121 L10.12477962996826 92.87088452104817 L12.07185263573139 95.23997587524248 L14.018925641494517 89.77291652902761 L15.965998647257644 90.98959547725472 L17.913071653020772 90.98959547725472 L19.8601446587839 105.96997484450178 L21.80721766454703 114.67246195722767 L23.754290670310155 118.2223925327436 L25.70136367607328 112.56681918919332 L27.64843668183641 118.67609135871675 L29.595509687599538 117.83801555297532 L31.542582693362665 119.2701905760426 L33.48965569912579 117.87744538951088 L35.436728704888914 113.70343153290673 L37.383801710652044 113.70343153290673 L39.33087471641517 99.1632446105316 L41.2779477221783 109.03365524390851 L43.22502072794143 108.47272107067258 L45.17209373370455 115.55065033402833 L47.11916673946768 112.07005950412427 L49.06623974523081 115.78725492382316 L51.01331275099393 107.09044448017048 L52.96038575675706 116.65490822108254 L54.90745876252019 104.62664736360473 L56.854531768283316 110.3696107261848 L58.801604774046446 104.34852126371491 L60.74867777980957 110.208311498645 L62.6957507855727 109.33039672706542 L64.64282379133583 106.08602181411875 L66.58989679709896 117.01753742136087 L68.53696980286207 110.65838441617409 L70.4840428086252 112.90929621426174 L72.43111581438833 116.10934196727453 L74.37818882015146 118.52367535115908 L76.3252618259146 118.52367535115908 L78.27233483167771 107.64310912737814 L80.21940783744084 110.09380387802896 L82.16648084320397 111.70106578613279 L84.1135538489671 116.92084226775563 L86.06062685473023 113.51929777616702 L88.00769986049336 116.75763291778446 L89.95477286625648 117.63396231331654 L91.9018458720196 118.03901822227178 L93.84891887778274 119.29942542176964 L95.79599188354587 117.33112224649312 L97.743064889309 119.65814232309211 L99.69013789507211 117.42090311488485 L101.63721090083524 119.15453227926307 L103.58428390659837 117.78193926794128 L105.5313569123615 119.63875982238267 L107.47842991812463 117.0740739768603 L109.42550292388776 120.29735827425931 L111.37257592965088 118.27776818384699 L113.31964893541401 119.28681145395966 L115.26672194117714 117.16167878877397 L117.21379494694027 119.42928561946479 L119.1608679527034 119.50078607920587 L121.10794095846651 119.86069968373836 L123.05501396422964 117.05928906668855 L125.00208696999277 112.50639079120315 L126.9491599757559 111.41878446676371 L128.89623298151903 119.74347391031834 L130.84330598728215 117.64007368227374 L132.7903789930453 114.44281512263473 L134.7374519988084 116.3834585999991 L136.68452500457153 119.25191528150825 L138.63159801033467 116.27401651156056 L140.5786710160978 119.57684065949624 L142.52574402186093 117.73494053930808 L144.47281702762405 119.66358629987448 L146.41989003338716 117.15333766511775 L148.3669630391503 118.61167139296833 L150.31403604491342 118.14236684116013 L152.26110905067657 113.30525666740914 L154.20818205643968 117.54987601340501 L156.1552550622028 118.90360049270373 L158.10232806796594 117.67588272448153 L160.04940107372906 119.32830739347324 L161.9964740794922 118.57669083759825 L163.94354708525532 114.27837582769769 L165.89062009101846 116.8526608694817 L167.83769309678158 118.21620445204216 L169.7847661025447 117.83614890053234 L171.73183910830784 119.3841918991467 L173.67891211407095 117.13710034592182 L175.6259851198341 119.70812002445966 L177.5730581255972 117.52782905811257 L179.52013113136033 113.83329173060186 L181.46720413712347 116.64891959091612 L183.4142771428866 120.33090432001222 L185.36135014864973 117.34640834006056 L187.30842315441285 117.8193311291384 L189.25549616017597 118.09272411440904 L191.2025691659391 114.17084386169053 L193.14964217170223 117.64078965855325 L195.09671517746537 118.61653747461082 L197.0437881832285 117.14431636399598 L198.9908611889916 113.57828143630748 L200.93793419475475 117

# Visualize data (radar plot) - Comparison of individuals from different generations, runs & configurations

In [22]:
// Input params for visualization START
val selectedIndividuals = mutableListOf<SelectedIndividual>()
selectedIndividuals.add(SelectedIndividual(0, 0, 100, 0)) // Individual at position
selectedIndividuals.add(SelectedIndividual(0, 0, 132, 0)) // Individual at position

val maxValues = mutableMapOf<String, Double>()
maxValues["SectorExploration"] = 5.0
maxValues["PowerUp_Pickup_Health"] = 10.0
maxValues["PowerUp_Pickup_Ammo"] = 15.0
maxValues["PowerUp_Pickup_Shield"] = 5.0
maxValues["MissilesFired"] = 20.0
maxValues["MissilesFiredAccuracy"] = 50.0
maxValues["SurvivalBonus"] = 5.0
maxValues["OpponentTrackingBonus"] = 5.0
maxValues["OpponentDestroyedBonus"] = 500.0
maxValues["DamageTakenPenalty"] = 50.0
// Input params for visualization END

// Prepare data for visualization
var selectedGPAlgorithmSolutionsSimple = mutableListOf<GPProgramSolutionSimple>()

// Get selected individuals
for (selectedIndividual in selectedIndividuals){
    // Prepare data
    val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
    val worstGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()

    prepareData(selectedIndividual.selectedConfiguration, selectedIndividual.selectedRun, bestGenIndividualsRating, worstGenIndividualsRating, null, null, null, null, null)

    var individual: GPProgramSolutionSimple?;
    if(selectedIndividual.bestWorstIndividual == 0) {
        individual = bestGenIndividualsRating[selectedIndividual.selectedGeneration]
    }
    else {
        individual = worstGenIndividualsRating[selectedIndividual.selectedGeneration]
    }

    selectedGPAlgorithmSolutionsSimple.add(individual!!)
}

// Find all fitness keys
val fitnessKeys = mutableListOf<String>()
for (individual in selectedGPAlgorithmSolutionsSimple) {
    for (key in individual.finalIndividualFitness.avgMatchResult.individualValues.keys) {
        if (key !in fitnessKeys) {
            fitnessKeys.add(key)
        }
    }
}

// Order fitnessKeys
fitnessKeys.sort()

// Build labels for visualization
val labels = mutableListOf<String>()
for (individual in selectedGPAlgorithmSolutionsSimple) {
    labels.addAll(fitnessKeys)
}

val datasets = mutableListOf<MutableList<Double>>()

// Build datasets for visualization
for (individual in selectedGPAlgorithmSolutionsSimple) {
    val dataset = mutableListOf<Double>()
    for (key in fitnessKeys) {
        if(individual.finalIndividualFitness.avgMatchResult.individualValues[key] == null) {
            dataset.add(0.0)
            System.out.println(key + ": 0.0")
            continue
        }
        dataset.add(Math.abs(individual.finalIndividualFitness.avgMatchResult.individualValues[key]!!) / maxValues[key]!!)
        System.out.println(key + ": " + individual.finalIndividualFitness.avgMatchResult.individualValues[key]!!)
    }
    System.out.println("/////////////////////////////")
    datasets.add(dataset)
}

var fitnessKeysIndexed = mutableListOf<Int>()
for (i in 0 until fitnessKeys.size) {
    fitnessKeysIndexed.add(i + 1)
}

var individualValueIdsMapped = mutableListOf<Int>()
var individualMapped = mutableListOf<String>()
var index = 0
for(dataset in datasets) {
    individualValueIdsMapped.addAll(fitnessKeysIndexed)
    individualMapped.addAll(List(fitnessKeys.size) { "Individual " + (index + 1) })
    index++
}

// Build map for visualization
val selectedIndividualsData = mapOf(
    "IndividualValueLabels" to labels,
    "IndividualValueId" to individualValueIdsMapped,
    "Individual" to individualMapped,
    "IndividualValues" to datasets.map { it }.toMutableList().flatten()
)

// Map each fitnessKey to a map 1 -> "fitnessKey1", 2 -> "fitnessKey2", ...
var labelsIndexed = fitnessKeys.mapIndexed { index, s -> index to s }.toMap().mapKeys { it.key + 1 }

letsPlot(selectedIndividualsData) +
        geomArea(flat = true) {   // <-- flat. I.e., do not transform segments to curves
            x = "IndividualValueId"; y = "IndividualValues"
        } +
        geomPoint() { x = "IndividualValueId"; y = "IndividualValues"; color="Individual" } +
        scaleXDiscrete(labels = labelsIndexed) +
        coordPolar()

DamageTakenPenalty: 13.609109
MissilesFired: -1.8181816
MissilesFiredAccuracy: -33.357548
OpponentDestroyedBonus: -306.81815
OpponentTrackingBonus: -2.312909
PowerUp_Pickup_Ammo: -5.6996818
PowerUp_Pickup_Health: -2.4242363
PowerUp_Pickup_Shield: -2.0887454
SectorExploration: -3.6969545
SurvivalBonus: -4.328909
/////////////////////////////
DamageTakenPenalty: 14.285708
MissilesFired: -0.72727275
MissilesFiredAccuracy: -23.181818
OpponentDestroyedBonus: -136.36363
OpponentTrackingBonus: -4.840273
PowerUp_Pickup_Ammo: -2.7954545
PowerUp_Pickup_Health: 0.0
PowerUp_Pickup_Shield: -1.4394001
SectorExploration: -2.0605907
SurvivalBonus: -5.0
/////////////////////////////


<path d="M170.5 100.04545454545456 L177.4057530686736 100.38471243900432 L184.24499996022723 101.39921888068147 L190.95187498838257 103.0792036188671 L197.46178728026769 105.40848748215933 L203.71204282183166 108.36463819363863 L209.642448235472 111.91918640595705 L215.19589047516592 116.03789987671627 L220.31888685632495 120.68111314367508 L224.96210012328373 125.80410952483408 L229.08081359404295 131.357551764528 L232.63536180636137 137.28795717816834 L235.59151251784067 143.53821271973231 L237.9207963811329 150.04812501161743 L239.60078111931853 156.7550000397728 L240.61528756099568 163.5942469313264 L240.95454545454544 170.5 L240.61528756099568 177.4057530686736 L239.60078111931853 184.2449999602272 L237.9207963811329 190.95187498838257 L235.59151251784067 197.46178728026769 L232.63536180636137 203.71204282183166 L229.08081359404298 209.64244823547196 L224.96210012328373 215.19589047516592 L220.31888685632495 220.31888685632492 L215.19589047516592 224.96210012328373 L209.64244823547196 229.08081359404298 L203.71204282183166 232.63536180636137 L197.46178728026769 235.59151251784067 L190.95187498838257 237.9207963811329 L184.24499996022723 239.60078111931853 L177.4057530686736 240.61528756099568 L170.5 240.95454545454544 L163.5942469313264 240.61528756099568 L156.75500003977277 239.60078111931853 L150.04812501161743 237.9207963811329 L143.53821271973231 235.59151251784067 L137.28795717816834 232.63536180636137 L131.35755176452804 229.08081359404298 L125.80410952483408 224.96210012328373 L120.68111314367506 220.31888685632495 L116.03789987671628 215.19589047516595 L111.91918640595703 209.642448235472 L108.36463819363863 203.71204282183166 L105.40848748215936 197.4617872802677 L103.07920361886711 190.95187498838257 L101.39921888068149 184.24499996022723 L100.3847124390043 177.40575306867356 L100.04545454545455 170.5 L100.3847124390043 163.59424693132644 L101.39921888068149 156.75500003977277 L103.0792036188671 150.04812501161746 L105.40848748215936 143.5382127197323 L108.36463819363863 137.28795717816834 L111.91918640595702 131.35755176452804 L116.03789987671627 125.80410952483408 L120.68111314367505 120.68111314367508 L125.80410952483405 116.03789987671627 L131.357551764528 111.91918640595705 L137.28795717816834 108.36463819363863 L143.53821271973226 105.40848748215936 L150.04812501161743 103.0792036188671 L156.75500003977277 101.3992188806815 L163.5942469313264 100.38471243900432 L170.5 100.04545454545456 " stroke="rgb(233,233,233)" stroke-opacity="1.0" stroke-width="1.0" fill="none">
 
 <path d="M170.5 29.590909090909122 L184.3115061373472 30.269424878008635 L197.98999992045444 32.29843776136295 L211.40374997676514 35.658407237734195 L224.42357456053537 40.31697496431866 L236.92408564366332 46.22927638727725 L248.78489647094398 53.3383728119141 L259.89178095033185 61.575799753432534 L270.1377737126499 70.86222628735015 L279.42420024656747 81.10821904966815 L287.6616271880859 92.21510352905605 L294.77072361272275 104.07591435633668 L300.68302503568134 116.57642543946463 L305.3415927622658 129.59625002323486 L308.70156223863705 143.01000007954556 L310.73057512199136 156.68849386265282 L311.4090909090909 170.5 L310.73057512199136 184.31150613734718 L308.70156223863705 197.98999992045444 L305.3415927622658 211.40374997676514 L300.68302503568134 224.42357456053537 L294.77072361272275 236.92408564366332 L287.66162718808596 248.78489647094392 L279.42420024656747 259.89178095033185 L270.1377737126499 270.13777371264985 L259.89178095033185 279.42420024656747 L248.78489647094392 287.66162718808596 L236.92408564366332 294.77072361272275 L224.42357456053537 300.68302503568134 L211.40374997676514 305.3415927622658 L197.98999992045447 308.70156223863705 L184.3115061373472 310.73057512199136 L170.5 311.4090909090909 L156.68849386265282 310.73057512199136 L143.01000007954553 308.70156223863705 L129.5962500232349 305.3415927622658 L116.57642543946463 300.68302503568134 L104.0759143563367 294.77072361272275 L92.2151035290561 287.661627188085

# Selected Individual Details

In [21]:
import org.jetbrains.letsPlot.intern.Plot

// Input params for visualization START
val selectedIndividuals = mutableListOf<SelectedIndividual>()
selectedIndividuals.add(SelectedIndividual(0, 0, 100, 0)) // Individual at position
selectedIndividuals.add(SelectedIndividual(0, 0, 130, 0)) // Individual at position
// Input params for visualization END

// Prepare data for visualization
var selectedGPAlgorithmSolutionsSimple = mutableListOf<GPProgramSolutionSimple>()

// Get selected individuals
for (selectedIndividual in selectedIndividuals){
    // Prepare data
    val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
    val worstGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()

    prepareData(selectedIndividual.selectedConfiguration, selectedIndividual.selectedRun, bestGenIndividualsRating, worstGenIndividualsRating, null, null, null, null, null)

    var individual: GPProgramSolutionSimple?;
    if(selectedIndividual.bestWorstIndividual == 0) {
        individual = bestGenIndividualAvgFitnesses[selectedIndividual.selectedGeneration]
    }
    else {
        individual = worstGenIndividualAvgFitnesses[selectedIndividual.selectedGeneration]
    }

    selectedGPAlgorithmSolutionsSimple.add(individual!!)
}

var plots = mutableListOf<Plot>()

var index = 0
for (individual in selectedGPAlgorithmSolutionsSimple) {
    var nodeCountsData = mapOf(
        "NodeName" to individual.nodeCounts.keys.toList(),
        "NodeCount" to individual.nodeCounts.values.toList()
    )

    val blankTheme = theme(line=elementBlank(), axis=elementBlank())
    val (w, h) = 800 to 400
    val p = letsPlot(nodeCountsData) + ggsize(w,h) + blankTheme

    val plot = p + geomPie(stat = Stat.identity,
            size = 20, stroke = 1, color = "white", hole = 0.5) { slice = "NodeCount"; fill = "NodeName" } +
            blankTheme +
            scaleFillBrewer(palette = "Set1") + ggtitle("Conf: " + selectedIndividuals[index].selectedConfiguration + " Run: " + selectedIndividuals[index].selectedRun + " Gen: " + selectedIndividuals[index].selectedGeneration + " IndividualID: " + individual.individualId)

    System.out.println(
        "Individual: " + "(Conf: " + selectedIndividuals[index].selectedConfiguration + " Run: " + selectedIndividuals[index].selectedRun + " Gen: " + selectedIndividuals[index].selectedGeneration + " IndividualID: " + individual.individualId + ")\nChangesCount: " + individual.changesCount + "\nFunctionNodesCount: " + individual.functionNodes + "\nTerminalNodesCount: " + individual.terminalNodes + "\nTreeSize: " + individual.treeSize + "\nTreeDepth: " + individual.treeDepth + "\nFitness: " + (individual.finalIndividualFitness.additionalValues["Rating"].toString() + ", " + individual.finalIndividualFitness.additionalValues["StdDeviation"]) + "\nIndividualAvgFitness: " + sumIndividualValues(individual.finalIndividualFitness.avgMatchResult) + "\nIndividualAvgFitnessValues: " + individual.finalIndividualFitness.avgMatchResult.individualValues.map { it.key + ": " + it.value }.toString()
        + "\n\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\"
    )

    index++

    plots.add(plot)
}

gggrid(plots, ncol = 2)

Individual: (Conf: 0 Run: 0 Gen: 100 IndividualID: 13278)
ChangesCount: 41
FunctionNodesCount: 61
TerminalNodesCount: 77
TreeSize: 138
TreeDepth: 11
Fitness: -48.83913, 2.8753748
IndividualAvgFitness: -348.93620660000005
IndividualAvgFitnessValues: [OpponentDestroyedBonus: -306.81815, PowerUp_Pickup_Health: -2.4242363, SectorExploration: -3.6969545, SurvivalBonus: -4.328909, DamageTakenPenalty: 13.609109, OpponentTrackingBonus: -2.312909, PowerUp_Pickup_Ammo: -5.6996818, PowerUp_Pickup_Shield: -2.0887454, MissilesFired: -1.8181816, MissilesFiredAccuracy: -33.357548]
\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\
Individual: (Conf: 0 Run: 0 Gen: 130 IndividualID: 13278)
ChangesCount: 85
FunctionNodesCount: 77
TerminalNodesCount: 91
TreeSize: 168
TreeDepth: 11
Fitness: -34.28788, 2.782343
IndividualAvgFitness: -313.34371905
IndividualAvgFitnessValues: [OpponentDestroyedBonus: -271.9697, SectorExploration: -3.909082, SurvivalBonus: -4.641727, DamageTakenPenalty: 10.6305, OpponentTracki

Conf: 0 Run: 0 Gen: 100 IndividualID: 13278 
 
 
 
 
 
 
 
 
 NodeName 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 RayHitObject 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Inverter 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Sequencer 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Rotate 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 ShieldLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 HealthLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 AmmoLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 MoveForward 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Shoot 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Selector 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Conf: 0 Run: 0 Gen: 130 IndividualID: 13278 
 
 
 
 
 
 
 
 
 NodeName 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 RayHitObject 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Inverter 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Sequencer 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 ShieldLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Rotate 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 HealthLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 AmmoLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 MoveForward 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Shoot 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Selector

# Genetic Diversity Graph
Genetic diversity of the population based on the avg fitness and node counts

### Calculation of genetic diversity between 2 individuals
1. Difference in avg fitness -> df
2. Difference in node counts -> dn
3. Normalize both values and multiply by the weights -> diversity = w1 * df_norm +  w2 * dn_norm


In [37]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
val w1 = 0.5
val w2 = 0.5
// Input params for visualization END

val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()

// Remove first 41 individuals


prepareData(selectedConfiguration, selectedRun, bestGenIndividualsRating, null, null, null, null, null)

val gpAlgorithmRunGeneticDiversity = mutableListOf<List<Double?>>()

var diversity = calculateDiversity(bestGenIndividualsRating[82], bestGenIndividualsRating[10], w1, w2)

for(i in 0 until bestGenIndividualsRating.size) {
    var gpAlgorithmGenGeneticDiversity = mutableListOf<Double?>()
    for (j in 0 until bestGenIndividualsRating.size) {
        if(j < i){
            var diversity = calculateDiversity(bestGenIndividualsRating[i], bestGenIndividualsRating[j], w1, w2)
            if(diversity > 1.0 || diversity < 0.0) {
                throw Exception("Diversity out of bounds: " + diversity + ", i: " + i + ", j:" + j)
            }
            gpAlgorithmGenGeneticDiversity.add(diversity)
        }
        else {
            gpAlgorithmGenGeneticDiversity.add(null)
        }
    }
    gpAlgorithmRunGeneticDiversity.add(gpAlgorithmGenGeneticDiversity)
}

var individuals = mutableListOf<Int>()
val generations = mutableListOf<String>()

for (i in 0 until gpAlgorithmRunGeneticDiversity.size) {
    generations.addAll(List(gpAlgorithmRunGeneticDiversity[i].size){(i + 1).toString()})

    for (i in 0 until gpAlgorithmRunGeneticDiversity[i].size) {
        individuals.add(i + 1)
    }
}

val df = dataFrameOf(
    "individuals" to individuals,
    "generations" to generations,
    "diversity" to gpAlgorithmRunGeneticDiversity.flatten()
)

val plot = letsPlot(df.toMap()) { x = "individuals"; y = "generations"; fill = "diversity" } + geomTile() + ggtitle("Genetic Diversity Graph")

plot

# Master Tournament Graph
Tournament between generation best individuals

In [15]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
// Input params for visualization END

val n = 3
val Generation = mutableListOf<Int>()
val Rating = mutableListOf<Double>()

val masterTournamentGraphData = progressData.multiConfigurationProgressData[selectedConfiguration].multiRunProgressData[selectedRun].masterTournamentGraphData;
for (i in 0 until masterTournamentGraphData.size) {
    Generation.addAll(List(n) {i + 1})
    val rating = Math.abs(masterTournamentGraphData[i].finalIndividualFitness.additionalValues["Rating"]!!)
    Rating.addAll(listOf(rating - (2*masterTournamentGraphData[i].finalIndividualFitness.additionalValues["StdDeviation"]!!), rating, rating + (2*masterTournamentGraphData[i].finalIndividualFitness.additionalValues["StdDeviation"]!!)))
}

val data = mapOf<String, Any>(
    "Generation" to Generation,
    "Rating" to Rating
)

letsPlot(data) { x = "Generation"; y = "Rating"}  + geomBoxplot(whiskerWidth = 0.2) + ggtitle("Convergence graph (Tournament between generation best individuals)")

0 
 
 
 
 
 
 
 
 
 20 
 
 
 
 
 
 
 
 
 40 
 
 
 
 
 
 
 
 
 60 
 
 
 
 
 
 
 
 
 80 
 
 
 
 
 
 
 
 
 100 
 
 
 
 
 
 
 
 
 
 
 0 
 
 
 
 
 
 
 10 
 
 
 
 
 
 
 20 
 
 
 
 
 
 
 30 
 
 
 
 
 
 
 40 
 
 
 
 
 
 
 50 
 
 
 
 
 
 
 
 
 Convergence graph (Tournament between generation best individuals) 
 
 
 
 
 Rating 
 
 
 
 
 Generation

# Convergence graph
Best individual in the final generation is matched with every best individual from previous generations

In [16]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
// Input params for visualization END

val convergenceGraphData = progressData.multiConfigurationProgressData[selectedConfiguration].multiRunProgressData[selectedRun].convergenceGraphData;

var generations = mutableListOf<String>()
var fitnesses = mutableListOf<Float>()

for (individualMatch in convergenceGraphData.finalIndividualFitness.individualMatchResults){
    generations.add(individualMatch.opponentsIDs[0].toString())
    fitnesses.add(individualMatch.value)
}

// Display data
val df = dataFrameOf(
    "Generation" to generations,
    "Fitness" to fitnesses
)

val plot = letsPlot(df.toMap()) { x = "Generation"; y = "Fitness"} + geomLine() + geomPoint(shape = 20) + ggtitle("Convergence graph")

plot

<path d="M1.0479633031436797 43.18150809158163 L1.0479633031436797 43.18150809158163 L6.287779818862077 195.87123379774755 L11.527596334580476 43.18150809158163 L16.76741285029887 44.25314111194056 L22.00722936601727 42.83649296853658 L27.24704588173567 44.25314111194056 L32.48686239745407 44.25314111194056 L37.72667891317247 44.25314111194056 L42.966495428890866 49.96252918110279 L48.20631194460926 49.96252918110279 L53.446128460327664 190.6137275728134 L58.68594497604606 46.37691651530652 L63.925761491764455 42.8343148230922 L69.16557800748285 42.8343148230922 L74.40539452320125 44.25314111194056 L79.64521103891964 44.25314111194056 L84.88502755463804 42.83649296853658 L90.12484407035645 42.83649296853658 L95.36466058607483 44.25314111194056 L100.60447710179324 52.94124666151977 L105.84429361751164 196.452150120394 L111.08411013323003 195.4062249277448 L116.32392664894843 52.94124666151977 L121.56374316466683 200.90686099134516 L126.80355968038522 195.4062249277448 L132.04337619610365 44.25314111194056 L137.28319271182204 42.83649296853658 L142.52300922754043 42.83649296853658 L147.76282574325884 42.83649296853658 L153.00264225897723 208.25355917376484 L158.24245877469562 42.83649296853658 L163.48227529041404 46.55582143797808 L168.72209180613243 44.25259696499759 L173.9619083218508 44.25314111194056 L179.20172483756923 38.47134307677531 L184.44154135328762 196.452150120394 L189.681357869006 295.96462983206834 L194.92117438472442 196.452150120394 L200.1609909004428 196.452150120394 L205.4008074161612 276.61637621231193 L210.64062393187962 177.95633799402714 L215.880440447598 44.25259696499759 L221.1202569633164 276.61637621231193 L226.3600734790348 184.56161727459477 L231.5998899947532 42.83649296853658 L236.8397065104716 188.14745424523775 L242.07952302619 188.14745424523775 L247.3193395419084 44.25259696499759 L252.55915605762678 295.96462983206834 L257.79897257334517 276.61637621231193 L263.0387890890636 44.25259696499759 L268.27860560478194 44.25259696499759 L273.51842212050036 295.96462983206834 L278.7582386362188 44.25259696499759 L283.99805515193714 187.8737026412014 L289.23787166765555 41.47592207525994 L294.47768818337397 186.69410837508335 L299.71750469909233 189.25528757558055 L304.95732121481075 44.25259696499759 L310.19713773052916 43.58009780419574 L315.4369542462475 186.98494037781776 L320.67677076196594 184.56161727459477 L325.91658727768436 43.58009780419574 L331.1564037934027 44.25259696499759 L336.39622030912113 200.8157766084047 L341.63603682483955 44.25259696499759 L346.8758533405579 190.41491040275397 L352.1156698562763 14.093553801527055 L357.35548637199474 44.25259696499759 L362.5953028877131 44.711946291414236 L367.8351194034315 272.60072130983986 L373.07493591914994 44.25259696499759 L378.3147524348683 180.2553795969957 L383.5545689505867 42.83594778314526 L388.79438546630513 253.97989661556997 L394.0342019820235 42.83594778314526 L399.2740184977419 42.83594778314526 L404.5138350134603 180.2553795969957 L409.7536515291787 14.093553801527055 L414.9934680448971 42.83594778314526 L420.2332845606155 253.97391515299088 L425.4731010763339 195.32024140317037 L430.7129175920523 42.83594778314526 L435.9527341077707 277.88592502955 L441.19255062348907 194.46007385394958 L446.4323671392075 253.97391515299088 L451.6721836549259 253.97391515299088 L456.91200017064426 28.452719329585925 L462.1518166863627 44.25259696499759 L467.3916332020811 44.25259696499759 L472.63144971779946 43.8325020252046 L477.8712662335179 253.97391515299088 L483.1110827492363 44.25259696499759 L488.35089926495465 43.8325020252046 L493.59071578067307 43.8325020252046 L498.8305322963915 253.97391515299088 L504.07034881210984 35.60472298195295 L509.31016532782826 26.75802144436524 L514.5499818435467 44.25259696499759 L519.7897983592651 42.83594778314526 L525.0296148749835 42.83594778314526 " fill="none" stroke-width="1.6500000000000001" stroke="rgb(71,71,71)" stroke-opacity="1.0">
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
